## Moscow metro data extraction

In [1]:
import numpy as np
import pandas as pd
import requests
from bs4 import BeautifulSoup
import re
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

In [2]:
# get html data from wiki link
link = 'https://en.wikipedia.org/wiki/List_of_Moscow_Metro_stations'
raw_data = requests.get(link).text
soup = BeautifulSoup(raw_data,'lxml')
My_table = soup.find('table',{'class':'wikitable sortable'})
#My_table

In [3]:
#parse html wiki table
station = []
lat = []
lon = []

for tr in My_table.find_all('tr'):
    td = tr.find_all('td')
    for k,word in enumerate(td):
        try:
            if k == 0:
                station.append(word.text.rstrip())
                #print(len(word.text.split()))
            if k == 6:
                q = word.text.split()

                lat.append(float(q[6].strip(';')))
                #s = re.sub(r"\ ", "", q[7])
                lon.append(float(q[7].strip("\ufeff ")))
        except IndexError:
            #print('index err')
            station.pop()

In [4]:
#create dataframe
d = { 'Station':station, 'Latitude':lat, 'Longitude':lon}
df = pd.DataFrame.from_dict(d)
df = df[['Station', 'Latitude','Longitude']]
df.drop([232], inplace = True)
df.head()

Station  Latitude  Longitude
0        Bulvar Rokossovskogo   55.8148    37.7342
1              Cherkizovskaya   55.8038    37.7448
2  Preobrazhenskaya Ploshchad   55.7963    37.7151
3                   Sokolniki   55.7888    37.6802
4              Krasnoselskaya   55.7801    37.6673

## Map

In [5]:
!conda install -c conda-forge geopy --yes 
!conda install -c conda-forge folium=0.5.0 --yes

Fetching package metadata .............
Solving package specifications: .

Package plan for installation in environment /opt/conda/envs/DSX-Python35:

The following NEW packages will be INSTALLED:

    geographiclib: 1.49-py_0   conda-forge
    geopy:         1.18.1-py_0 conda-forge

geographiclib- 100% |################################| Time: 0:00:00  22.70 MB/s
geopy-1.18.1-p 100% |################################| Time: 0:00:00  37.85 MB/s
Fetching package metadata .............
Solving package specifications: .

Package plan for installation in environment /opt/conda/envs/DSX-Python35:

The following NEW packages will be INSTALLED:

    altair:  2.2.2-py35_1 conda-forge
    branca:  0.3.1-py_0   conda-forge
    folium:  0.5.0-py_0   conda-forge
    vincent: 0.4.4-py_1   conda-forge

altair-2.2.2-p 100% |################################| Time: 0:00:00  54.93 MB/s
branca-0.3.1-p 100% |################################| Time: 0:00:00  35.13 MB/s
vincent-0.4.4- 100% |###################

!conda clean --index-cache

In [6]:
from geopy.geocoders import Nominatim
import matplotlib.pyplot as plt
import folium
import json
import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe
from sklearn.cluster import KMeans
import matplotlib.cm as cm
import matplotlib.colors as colors

In [7]:
address = 'Moscow'

geolocator = Nominatim()
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of Manhattan are {}, {}.'.format(latitude, longitude))

/opt/conda/envs/DSX-Python35/lib/python3.5/site-packages/ipykernel/__main__.py:3: DeprecationWarning: Using Nominatim with the default "geopy/1.18.1" `user_agent` is strongly discouraged, as it violates Nominatim's ToS https://operations.osmfoundation.org/policies/nominatim/ and may possibly cause 403 and 429 HTTP errors. Please specify a custom `user_agent` with `Nominatim(user_agent="my-application")` or by overriding the default `user_agent`: `geopy.geocoders.options.default_user_agent = "my-application"`. In geopy 2.0 this will become an exception.
  app.launch_new_instance()


The geograpical coordinate of Manhattan are 55.7507178, 37.6176606.


In [8]:
map_msc= folium.Map(location=[latitude, longitude], zoom_start=11)

# add markers to map
for lat, lng, station in zip(df['Latitude'], df['Longitude'],  df['Station']):
    label = '{}'.format(station)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_msc)  
    
map_msc

## Data extraction via Foursquare

In [9]:

VERSION = '20180605' # Foursquare API version

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: XDMAGY5KTTWCGBLMTH2T2TBYSAYOAADKO1OM4AGC12A2PVLJ
CLIENT_SECRET:3NCMLNAZUBJV5NYMUDLF4H3PPQ1UEUZ0JPL1GLBTBXWWK0LW


In [10]:
LIMIT = 100 # limit of number of venues returned by Foursquare API

radius = 500 # define radius

In [11]:
def getNearbyVenues(names, latitudes, longitudes, radius=500):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Station', 
                  'Station Latitude', 
                  'Station Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

In [12]:
msc_venues = getNearbyVenues(names=df['Station'],
                                   latitudes=df['Latitude'],
                                   longitudes=df['Longitude']
                                  )

Bulvar Rokossovskogo
Cherkizovskaya
Preobrazhenskaya Ploshchad
Sokolniki
Krasnoselskaya
Komsomolskaya
Krasnye Vorota
Chistyye Prudy
Lubyanka
Okhotny Ryad
Biblioteka Imeni Lenina
Kropotkinskaya
Park Kultury
Frunzenskaya
Sportivnaya
Vorobyovy Gory
Universitet
Prospekt Vernadskogo
Yugo-Zapadnaya
Troparyovo
Rumyantsevo
Salaryevo
Khovrino
Belomorskaya
Rechnoy Vokzal
Vodny Stadion
Voykovskaya
Sokol
Aeroport
Dinamo
Belorusskaya
Mayakovskaya
Tverskaya
Teatralnaya
Novokuznetskaya
Paveletskaya
Avtozavodskaya
Tekhnopark
Kolomenskaya
Kashirskaya
Kantemirovskaya
Tsaritsyno
Orekhovo
Domodedovskaya
Krasnogvardeyskaya
Alma-Atinskaya
Pyatnitskoye Shosse
Mitino
Volokolamskaya
Myakinino
Strogino
Krylatskoye
Molodyozhnaya
Kuntsevskaya
Slavyansky Bulvar
Park Pobedy
Kiyevskaya
Smolenskaya
Arbatskaya
Ploshchad Revolyutsii
Kurskaya
Baumanskaya
Elektrozavodskaya
Semyonovskaya
Partizanskaya
Izmaylovskaya
Pervomayskaya
Shchyolkovskaya
Kuntsevskaya
Pionerskaya
Filyovsky Park
Bagrationovskaya
Fili
Kutuzovskaya
Stu

In [13]:
print(msc_venues.shape)
msc_venues.head()

(9061, 7)


Station  Station Latitude  Station Longitude  \
0  Bulvar Rokossovskogo           55.8148            37.7342   
1  Bulvar Rokossovskogo           55.8148            37.7342   
2  Bulvar Rokossovskogo           55.8148            37.7342   
3  Bulvar Rokossovskogo           55.8148            37.7342   
4  Bulvar Rokossovskogo           55.8148            37.7342   

                 Venue  Venue Latitude  Venue Longitude     Venue Category  
0             Подружка       55.814523        37.736781     Cosmetics Shop  
1          Бургер Кинг       55.814026        37.733659       Burger Joint  
2  Галерея Богородское       55.813944        37.734298        Art Gallery  
3              Мегафон       55.815595        37.737622  Mobile Phone Shop  
4        Coffeetasters       55.814610        37.733290        Coffee Shop

In [14]:

# analyze each neighbourhood
# one hot encoding
msc_onehot = pd.get_dummies(msc_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
msc_onehot['Station'] = msc_venues['Station'] 

# move neighborhood column to the first column
fixed_columns = [msc_onehot.columns[-1]] + list(msc_onehot.columns[:-1])
msc_onehot = msc_onehot[fixed_columns]

msc_onehot.head()

Station  ATM  Accessories Store  Adult Boutique  \
0  Bulvar Rokossovskogo    0                  0               0   
1  Bulvar Rokossovskogo    0                  0               0   
2  Bulvar Rokossovskogo    0                  0               0   
3  Bulvar Rokossovskogo    0                  0               0   
4  Bulvar Rokossovskogo    0                  0               0   

   American Restaurant  Amphitheater  Arcade  Argentinian Restaurant  \
0                    0             0       0                       0   
1                    0             0       0                       0   
2                    0             0       0                       0   
3                    0             0       0                       0   
4                    0             0       0                       0   

   Art Gallery  Art Museum  Arts & Crafts Store  Arts & Entertainment  \
0            0           0                    0                     0   
1            0           0                    0                     0   
2            1           0                    0                     0   
3            0           0                    0                     0   
4            0           0                    0                     0   

   Asian Restaurant  Athletics & Sports  Auto Dealership  Auto Workshop  \
0                 0                   0                0              0   
1                 0                   0                0              0   
2                 0                   0                0              0   
3                 0                   0                0              0   
4                 0                   0                0              0   

   BBQ Joint  Baby Store  Bagel Shop  Bakery  Bank  Bar  Baseball Field  \
0          0           0           0       0     0    0               0   
1          0           0           0       0     0    0               0   
2          0           0           0       0     0    0               0   
3          0           0           0       0     0    0               0   
4          0           0           0       0     0    0               0   

   Basketball Court  Bath House  Beach  Bed & Breakfast  Beer Bar  Beer Store  \
0                 0           0      0                0         0           0   
1                 0           0      0                0         0           0   
2                 0           0      0                0         0           0   
3                 0           0      0                0         0           0   
4                 0           0      0                0         0           0   

   Belgian Restaurant  Betting Shop  Big Box Store  Bike Rental / Bike Share  \
0                   0             0              0                         0   
1                   0             0              0                         0   
2                   0             0              0                         0   
3                   0             0              0                         0   
4                   0             0              0                         0   

   Bike Shop  Bistro  Blini House  Board Shop  Boat Rental  Boat or Ferry  \
0          0       0            0           0            0              0   
1          0       0            0           0            0              0   
2          0       0            0           0            0              0   
3          0       0            0           0            0              0   
4          0       0            0           0            0              0   

   Bookstore  Botanical Garden  Boutique  Bowling Alley  Boxing Gym  \
0          0                 0         0              0           0   
1          0                 0         0              0           0   
2          0                 0         0              0           0   
3          0                 0         0              0           0   
4          0                 0         0             

In [15]:
msc_grouped = msc_onehot.groupby('Station').mean().reset_index()
msc_grouped

Station       ATM  Accessories Store  Adult Boutique  \
0                       Aeroport  0.000000           0.000000        0.000000   
1                Akademicheskaya  0.000000           0.000000        0.000000   
2             Aleksandrovsky Sad  0.000000           0.000000        0.000000   
3                 Alekseyevskaya  0.000000           0.000000        0.000000   
4                 Alma-Atinskaya  0.000000           0.000000        0.000000   
5                      Altufyevo  0.000000           0.000000        0.000000   
6                     Andronovka  0.000000           0.000000        0.000000   
7                         Annino  0.000000           0.000000        0.000000   
8                     Arbatskaya  0.000000           0.000000        0.000000   
9                  Aviamotornaya  0.000000           0.000000        0.000000   
10                Avtozavodskaya  0.000000           0.000000        0.000000   
11                Babushkinskaya  0.000000           0.000000        0.000000   
12              Bagrationovskaya  0.000000           0.000000        0.000000   
13                   Baltiyskaya  0.000000           0.000000        0.000000   
14                  Barrikadnaya  0.000000           0.000000        0.000000   
15                   Baumanskaya  0.000000           0.000000        0.000000   
16                      Begovaya  0.000000           0.000000        0.000000   
17                 Belokamennaya  0.000000           0.000000        0.000000   
18                  Belomorskaya  0.000000           0.000000        0.000000   
19                  Belorusskaya  0.000000           0.000000        0.000000   
20                     Belyayevo  0.000000           0.000000        0.000000   
21                      Bibirevo  0.000000           0.047619        0.000000   
22       Biblioteka Imeni Lenina  0.000000           0.000000        0.000000   
23               Bittsevsky Park  0.000000           0.000000        0.000000   
24                      Borisovo  0.000000           0.000000        0.000000   
25                  Borovitskaya  0.000000           0.000000        0.000000   
26              Botanichesky Sad  0.000000           0.000000        0.000000   
27                Bratislavskaya  0.000000           0.000000        0.000000   
28      Bulvar Admirala Ushakova  0.000000           0.000000        0.000000   
29      Bulvar Dmitriya Donskogo  0.000000           0.000000        0.000000   
30          Bulvar Rokossovskogo  0.000000           0.000000        0.000000   
31             Buninskaya Alleya  0.000000           0.000000        0.000000   
32                    Butyrskaya  0.000000           0.000000        0.000000   
33                  Chekhovskaya  0.000000           0.000000        0.000000   
34                Cherkizovskaya  0.000000           0.000000        0.000000   
35                Chertanovskaya  0.000000           0.000000        0.000000   
36                Chistyye Prudy  0.000000           0.000000        0.000000   
37                  Chkalovskaya  0.000000           0.000000        0.000000   
38                Delovoy Tsentr  0.000000           0.000000        0.000000   
39                        Dinamo  0.000000           0.000000        0.052632   
40                  Dmitrovskaya  0.000000           0.024096        0.000000   
41                 Dobryninskaya  0.000000           0.000000        0.000000   
42                Domodedovskaya  0.000000           0.000000        0.000000   
43                 Dostoyevskaya  0.000000           0.000000        0.000000   
44                      Dubrovka  0.000000           0.000000        0.000000   
45             Elektrozavodskaya  0.000000           0.000000        0.000000   
46                          Fili  0.000000           0.000000        0.034483   
47                Filyovsky Park  0.000000           0.000000        0.000000   
48                 Fonvizinskaya  0.000000           0.0

In [16]:
num_top_venues = 5

for hood in msc_grouped['Station']:
    print("----"+hood+"----")
    temp = msc_grouped[msc_grouped['Station'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----Aeroport----
               venue  freq
0        Coffee Shop  0.12
1               Café  0.07
2             Bakery  0.07
3     Cosmetics Shop  0.05
4  Convenience Store  0.04


----Akademicheskaya----
           venue  freq
0       Pharmacy  0.09
1  Grocery Store  0.07
2      Bookstore  0.05
3    Pizza Place  0.05
4           Park  0.05


----Aleksandrovsky Sad----
                  venue  freq
0                 Plaza  0.09
1          Concert Hall  0.09
2                  Park  0.06
3  Caucasian Restaurant  0.04
4            Restaurant  0.04


----Alekseyevskaya----
               venue  freq
0        Coffee Shop  0.05
1  Health Food Store  0.05
2   Toy / Game Store  0.05
3         Hobby Shop  0.05
4             Office  0.03


----Alma-Atinskaya----
               venue  freq
0           Bus Stop  0.17
1               Park  0.08
2   Pedestrian Plaza  0.08
3               Lake  0.08
4  Convenience Store  0.08


----Altufyevo----
                  venue  freq
0              Pharmacy 

In [17]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

## restart here

In [18]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Station']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
venues_sorted = pd.DataFrame(columns=columns)
venues_sorted['Station'] = msc_grouped['Station']

for ind in np.arange(msc_grouped.shape[0]):
    venues_sorted.iloc[ind, 1:] = return_most_common_venues(msc_grouped.iloc[ind, :], num_top_venues)

venues_sorted.head()

Station 1st Most Common Venue 2nd Most Common Venue  \
0            Aeroport           Coffee Shop                  Café   
1     Akademicheskaya              Pharmacy         Grocery Store   
2  Aleksandrovsky Sad                 Plaza          Concert Hall   
3      Alekseyevskaya            Hobby Shop     Health Food Store   
4      Alma-Atinskaya              Bus Stop     Convenience Store   

  3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
0                Bakery        Cosmetics Shop              Pharmacy   
1             Bookstore           Pizza Place                  Park   
2                  Park            Restaurant        History Museum   
3      Toy / Game Store           Coffee Shop    Italian Restaurant   
4      Pedestrian Plaza     Health Food Store                  Lake   

  6th Most Common Venue        7th Most Common Venue 8th Most Common Venue  \
0     Convenience Store                  Flower Shop  Caucasian Restaurant   
1            Restaurant                 Cocktail Bar     College Cafeteria   
2  Caucasian Restaurant                       Museum        Science Museum   
3          Gourmet Shop  Eastern European Restaurant    Photography Studio   
4   Arts & Crafts Store                   Playground                   Gym   

        9th Most Common Venue 10th Most Common Venue  
0  Modern European Restaurant         Massage Studio  
1                 Coffee Shop             Smoke Shop  
2                 Coffee Shop         Sandwich Place  
3                   Pet Store      Mobile Phone Shop  
4                    Pharmacy                   Park

In [19]:
#cluster neighboorhoods
# set number of clusters
kclusters = 6

msc_grouped_clustering = msc_grouped.drop('Station', 1)

# run k-means clustering
#kmeans = KMeans(n_clusters=kclusters,algorithm = 'full', random_state = 0).fit(msc_grouped_clustering)

kmeans = KMeans(n_clusters=kclusters,algorithm = 'elkan', random_state = 0, init = 'random',max_iter = 1000).fit(msc_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:100]

array([0, 2, 0, 5, 2, 3, 1, 3, 0, 3, 5, 3, 3, 5, 5, 5, 0, 2, 1, 0, 3, 3, 0,
       1, 1, 0, 1, 2, 3, 3, 3, 1, 3, 5, 2, 3, 5, 5, 5, 2, 5, 0, 3, 2, 2, 5,
       3, 3, 3, 0, 5, 3, 3, 5, 3, 3, 2, 1, 5, 5, 3, 0, 3, 1, 3, 5, 3, 2, 5,
       0, 5, 0, 3, 5, 2, 5, 5, 3, 5, 2, 3, 4, 2, 2, 0, 5, 0, 3, 5, 3, 3, 5,
       3, 0, 5, 2, 3, 0, 5, 2], dtype=int32)

In [20]:
venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)
venues_sorted.head()

Cluster Labels             Station 1st Most Common Venue  \
0               0            Aeroport           Coffee Shop   
1               2     Akademicheskaya              Pharmacy   
2               0  Aleksandrovsky Sad                 Plaza   
3               5      Alekseyevskaya            Hobby Shop   
4               2      Alma-Atinskaya              Bus Stop   

  2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
0                  Café                Bakery        Cosmetics Shop   
1         Grocery Store             Bookstore           Pizza Place   
2          Concert Hall                  Park            Restaurant   
3     Health Food Store      Toy / Game Store           Coffee Shop   
4     Convenience Store      Pedestrian Plaza     Health Food Store   

  5th Most Common Venue 6th Most Common Venue        7th Most Common Venue  \
0              Pharmacy     Convenience Store                  Flower Shop   
1                  Park            Restaurant                 Cocktail Bar   
2        History Museum  Caucasian Restaurant                       Museum   
3    Italian Restaurant          Gourmet Shop  Eastern European Restaurant   
4                  Lake   Arts & Crafts Store                   Playground   

  8th Most Common Venue       9th Most Common Venue 10th Most Common Venue  
0  Caucasian Restaurant  Modern European Restaurant         Massage Studio  
1     College Cafeteria                 Coffee Shop             Smoke Shop  
2        Science Museum                 Coffee Shop         Sandwich Place  
3    Photography Studio                   Pet Store      Mobile Phone Shop  
4                   Gym                    Pharmacy                   Park

In [21]:
merged = df
merged = merged.join(venues_sorted.set_index('Station'), on='Station')
merged.head()

Station  Latitude  Longitude  Cluster Labels  \
0        Bulvar Rokossovskogo   55.8148    37.7342               3   
1              Cherkizovskaya   55.8038    37.7448               2   
2  Preobrazhenskaya Ploshchad   55.7963    37.7151               0   
3                   Sokolniki   55.7888    37.6802               5   
4              Krasnoselskaya   55.7801    37.6673               5   

  1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue  \
0              Bus Line        Cosmetics Shop          Burger Joint   
1   Sporting Goods Shop          Soccer Field        Soccer Stadium   
2          Dance Studio           Coffee Shop     Health Food Store   
3   Sporting Goods Shop          Dessert Shop            Board Shop   
4  Fast Food Restaurant           Coffee Shop                Arcade   

  4th Most Common Venue  5th Most Common Venue 6th Most Common Venue  \
0           Bridal Shop            Supermarket      Sushi Restaurant   
1  Gym / Fitness Center             Sports Bar           Bus Station   
2                  Café                 Arcade                Bakery   
3     Health Food Store            Coffee Shop        Clothing Store   
4          Dance Studio  Vietnamese Restaurant       Bed & Breakfast   

  7th Most Common Venue       8th Most Common Venue 9th Most Common Venue  \
0             Gift Shop               Grocery Store    Tex-Mex Restaurant   
1    Light Rail Station                Hockey Arena     Martial Arts Dojo   
2                Bistro        Herbs & Spices Store              Bus Stop   
3      Toy / Game Store  Modern European Restaurant  Gym / Fitness Center   
4        Clothing Store        Gym / Fitness Center           Flower Shop   

  10th Most Common Venue  
0      Mobile Phone Shop  
1            Pizza Place  
2         Farmers Market  
3              Bike Shop  
4            Music Venue

In [22]:
for i in range(kclusters):
    print(len(merged.loc[merged['Cluster Labels']  == i]))

44
11
43
79
4
65


In [23]:
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(merged['Latitude'], merged['Longitude'], merged['Station'], merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
map_clusters

In [24]:
map_clusters_1 = folium.Map(tiles = 'Stamen Toner',location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(merged['Latitude'], merged['Longitude'], merged['Station'], merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters_1)
map_clusters_1

## Examine cluster

In [25]:
merged.loc[merged['Cluster Labels'] == 0, merged.columns[[1] + list(range( merged.shape[1]))]]

Latitude                     Station  Latitude  Longitude  \
2     55.7963  Preobrazhenskaya Ploshchad   55.7963    37.7151   
5     55.7753               Komsomolskaya   55.7753    37.6562   
6     55.7690              Krasnye Vorota   55.7690    37.6487   
10    55.7512     Biblioteka Imeni Lenina   55.7512    37.6100   
11    55.7453              Kropotkinskaya   55.7453    37.6037   
12    55.7356                Park Kultury   55.7356    37.5943   
13    55.7267                Frunzenskaya   55.7267    37.5786   
14    55.7233                 Sportivnaya   55.7233    37.5639   
27    55.8051                       Sokol   55.8051    37.5153   
28    55.8003                    Aeroport   55.8003    37.5329   
30    55.7767                Belorusskaya   55.7767    37.5835   
34    55.7415             Novokuznetskaya   55.7415    37.6295   
52    55.7408               Molodyozhnaya   55.7408    37.4168   
55    55.7362                 Park Pobedy   55.7362    37.5182   
57    55.7474                 Smolenskaya   55.7474    37.5823   
58    55.7522                  Arbatskaya   55.7522    37.6061   
78    55.7488                 Smolenskaya   55.7488    37.5825   
79    55.7518                  Arbatskaya   55.7518    37.6007   
80    55.7525          Aleksandrovsky Sad   55.7525    37.6085   
83    55.7764                Belorusskaya   55.7764    37.5844   
84    55.7799             Novoslobodskaya   55.7799    37.6028   
85    55.7798               Prospekt Mira   55.7798    37.6318   
86    55.7748               Komsomolskaya   55.7748    37.6549   
90    55.7291               Dobryninskaya   55.7291    37.6243   
91    55.7297                Oktyabrskaya   55.7297    37.6091   
92    55.7357                Park Kultury   55.7357    37.5915   
100   55.7812               Prospekt Mira   55.7812    37.6318   
101   55.7733               Sukharevskaya   55.7733    37.6319   
104   55.7412              Tretyakovskaya   55.7412    37.6274   
105   55.7306                Oktyabrskaya   55.7306    37.6112   
124   55.7738                    Begovaya   55.7738    37.5468   
140   55.6975                     Ramenki   55.6975    37.4984   
141   55.7069       Lomonosovsky Prospekt   55.7069    37.5156   
143   55.7362                 Park Pobedy   55.7362    37.5182   
144   55.7412              Tretyakovskaya   55.7412    37.6274   
146   55.7472           Ploshchad Ilyicha   55.7472    37.6824   
160   55.7810             Mendeleyevskaya   55.7810    37.6011   
163   55.7511                Borovitskaya   55.7511    37.6072   
164   55.7379                    Polyanka   55.7379    37.6180   
165   55.7280              Serpukhovskaya   55.7280    37.6246   
188   55.7463                    Rimskaya   55.7463    37.6819   
198   55.6211               Shipilovskaya   55.6211    37.7437   
236   55.7203                    Luzhniki   55.7203    37.5631   
243   55.8136                  Streshnevo   55.8136    37.4869   

     Cluster Labels      1st Most Common Venue 2nd Most Common Venue  \
2                 0               Dance Studio           Coffee Shop   
5                 0                       Café                Bakery   
6                 0                Coffee Shop            Restaurant   
10                0             History Museum           Coffee Shop   
11                0                 Art Museum           Coffee Shop   
12                0                Coffee Shop                Bakery   
13                0                Coffee Shop  Gym / Fitness Center   
14                0                     Bakery        Gymnastics Gym   
27                0                     Bakery                  Café   
28                0                Coffee Shop                  Café   
30                0               Burger Joint            Restaurant   
34                0                  Bookstore           Yoga Studio   
52                0                     Bakery           Coffee Shop   
55                0       

In [26]:
merged.loc[merged['Cluster Labels'] == 1, merged.columns[[1] + list(range( merged.shape[1]))]]

Latitude            Station  Latitude  Longitude  Cluster Labels  \
22    55.8791           Khovrino   55.8791    37.4822               1   
23    55.8658       Belomorskaya   55.8658    37.4764               1   
96    55.8449   Botanichesky Sad   55.8449    37.6383               1   
116   55.6010   Novoyasenevskaya   55.6010    37.5541               1   
193   55.6909         Volzhskaya   55.6909    37.7530               1   
197   55.6334           Borisovo   55.6334    37.7436               1   
203   55.6004    Bittsevsky Park   55.6004    37.5562               1   
209   55.5380  Buninskaya Alleya   55.5380    37.5158               1   
218   55.8460   Botanichesky Sad   55.8460    37.6413               1   
226   55.7411         Andronovka   55.7411    37.7344               1   
245   55.8397            Koptevo   55.8397    37.5203               1   

    1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue  \
22            Supermarket            Restaurant            Skate Park   
23                Brewery           Supermarket            Playground   
96                   Park           Supermarket            Sports Bar   
116            Restaurant         Metro Station               Stables   
193                  Park                Bakery              Bus Stop   
197           Supermarket     Convenience Store              Bus Stop   
203         Historic Site               Stables            Beer Store   
209                  Park           Supermarket             Pet Store   
218                  Park           Supermarket            Sports Bar   
226           Music Venue           Supermarket         Shopping Mall   
245              Bus Stop              Pharmacy           Supermarket   

      4th Most Common Venue    5th Most Common Venue 6th Most Common Venue  \
22                 Bus Stop              Coffee Shop                   Gym   
23        Convenience Store                     Park            Food Truck   
96   Furniture / Home Store         Recording Studio    Light Rail Station   
116                    Park                      Gym            Beer Store   
193                Fountain              Fish Market         Fishing Store   
197              Food Truck             Tennis Court                  Park   
203           Metro Station                     Park            Restaurant   
209     Japanese Restaurant  Health & Beauty Service           Art Gallery   
218  Furniture / Home Store         Recording Studio    Light Rail Station   
226                   Diner                 Bus Stop            Food Truck   
245           Historic Site                     Park         Grocery Store   

          7th Most Common Venue 8th Most Common Venue 9th Most Common Venue  \
22                   Playground                  Park                  Food   
23                  Fish Market         Fishing Store           Flea Market   
96   Construction & Landscaping           Record Shop           Music Store   
116                 Supermarket         Historic Site                 Diner   
193                 Flea Market           Flower Shop                  Food   
197                         Gym         Metro Station                  Tree   
203     Fruit & Vegetable Store    Frozen Yogurt Shop  Fast Food Restaurant   
209         Fried Chicken Joint          Liquor Store     Food & Drink Shop   
218  Construction & Landscaping           Record Shop           Music Store   
226                 Fish Market         Fishing Store           Flea Market   
245           Convenience Store         Train Station              Bus Line   

         10th Most Common Venue  
22   Financial or Legal Service  
23                  Flower Shop  
96   Financial or Legal Service  
116  Financial or Legal Service  
193           Food & Drink Shop  
197                 Coffee Shop  
203  Financial or Legal Service  
209  Financial or Legal Service  
218  Financial or Legal Service  
226                 Flowe

In [27]:
merged.loc[merged['Cluster Labels'] == 2, merged.columns[[1] + list(range( merged.shape[1]))]]

Latitude                Station  Latitude  Longitude  Cluster Labels  \
1     55.8038         Cherkizovskaya   55.8038   37.74480               2   
15    55.7103         Vorobyovy Gory   55.7103   37.55920               2   
29    55.7897                 Dinamo   55.7897   37.55800               2   
45    55.6326         Alma-Atinskaya   55.6326   37.76600               2   
53    55.7307           Kuntsevskaya   55.7307   37.44590               2   
64    55.7886          Partizanskaya   55.7886   37.75060               2   
68    55.7307           Kuntsevskaya   55.7307   37.44590               2   
82    55.7613     Krasnopresnenskaya   55.7613   37.57740               2   
97    55.8211                  VDNKh   55.8211   37.64110               2   
107   55.7077      Leninsky Prospekt   55.7077   37.58610               2   
108   55.6877        Akademicheskaya   55.6877   37.57330               2   
110   55.6702     Novye Cheryomushki   55.6702   37.55440               2   
120   55.8182                Spartak   55.8182   37.43520               2   
125   55.7650       Ulitsa 1905 Goda   55.7650   37.56130               2   
132   55.7253  Volgogradsky Prospekt   55.7253   37.68690               2   
133   55.7088         Tekstilshchiki   55.7088   37.73160               2   
142   55.7246               Minskaya   55.7246   37.49700               2   
148   55.7576     Shosse Entuziastov   55.7576   37.75000               2   
155   55.8473              Vladykino   55.8473   37.58990               2   
167   55.6830           Nagatinskaya   55.6830   37.62240               2   
168   55.6724              Nagornaya   55.6724   37.61040               2   
169   55.6627   Nakhimovsky Prospekt   55.6627   37.60550               2   
179   55.8460             Okruzhnaya   55.8460   37.57425               2   
184   55.7816          Dostoyevskaya   55.7816   37.61510               2   
190   55.7186               Dubrovka   55.7186   37.67600               2   
195   55.6597         Bratislavskaya   55.6597   37.75050               2   
211   55.8218    Ulitsa Milashenkova   55.8218   37.59110               2   
212   55.8218             Teletsentr   55.8218   37.60890               2   
216   55.8472             Okruzhnaya   55.8472   37.56940               2   
217   55.8476              Vladykino   55.8476   37.59300               2   
219   55.8400              Rostokino   55.8400   37.66530               2   
220   55.8300          Belokamennaya   55.8300   37.70060               2   
222   55.8039              Lokomotiv   55.8039   37.74600               2   
224   55.7714        Sokolinaya Gora   55.7714   37.74510               2   
225   55.7590     Shosse Entuziastov   55.7590   37.74630               2   
228   55.7239      Novokhokhlovskaya   55.7239   37.71610               2   
229   55.7183            Ugreshskaya   55.7183   37.69780               2   
230   55.7183               Dubrovka   55.7183   37.69780               2   
233   55.6900         Verkhnie Kotly   55.6900   37.61890               2   
235   55.7069     Ploshchad Gagarina   55.7069   37.58580               2   
240   55.7772            Khoroshyovo   55.7772   37.50720               2   
242   55.7991          Panfilovskaya   55.7991   37.49880               2   
246   55.8472              Likhobory   55.8472   37.55130               2   

           1st Most Common Venue  2nd Most Common Venue  \
1            Sporting Goods Shop           Soccer Field   
15                         Train     Athletics & Sports   
29                          Park              Wine Shop   
45                      Bus Stop      Convenience Store   
53                       Theater                  Beach   
64   Eastern European Restaurant             Restaurant   
68                       Theater                  Beach   
82                   Planetarium            Zoo Exhibit   
97                          Café              Nightclub   
107          Sporting Good

In [28]:
merged.loc[merged['Cluster Labels'] == 3, merged.columns[[1] + list(range( merged.shape[1]))]]

Latitude                      Station   Latitude  Longitude  \
0    55.814800         Bulvar Rokossovskogo  55.814800  37.734200   
17   55.677100         Prospekt Vernadskogo  55.677100  37.506000   
18   55.663700               Yugo-Zapadnaya  55.663700  37.483300   
19   55.645900                   Troparyovo  55.645900  37.472500   
38   55.678500                 Kolomenskaya  55.678500  37.663800   
39   55.655100                  Kashirskaya  55.655100  37.648700   
40   55.635800              Kantemirovskaya  55.635800  37.656400   
41   55.621400                   Tsaritsyno  55.621400  37.669400   
42   55.613200                     Orekhovo  55.613200  37.694900   
43   55.610800               Domodedovskaya  55.610800  37.718600   
44   55.613700           Krasnogvardeyskaya  55.613700  37.744400   
46   55.856300          Pyatnitskoye Shosse  55.856300  37.354400   
47   55.845700                       Mitino  55.845700  37.362200   
48   55.835400               Volokolamskaya  55.835400  37.382200   
50   55.803800                     Strogino  55.803800  37.403100   
51   55.756700                  Krylatskoye  55.756700  37.408100   
54   55.729600            Slavyansky Bulvar  55.729600  37.470600   
65   55.787800                Izmaylovskaya  55.787800  37.781400   
66   55.794800                Pervomayskaya  55.794800  37.799300   
67   55.809400              Shchyolkovskaya  55.809400  37.798600   
69   55.736000                  Pionerskaya  55.736000  37.467100   
70   55.739600               Filyovsky Park  55.739600  37.483300   
71   55.743800             Bagrationovskaya  55.743800  37.497700   
72   55.746000                         Fili  55.746000  37.515000   
93   55.887200                   Medvedkovo  55.887200  37.661300   
94   55.869400               Babushkinskaya  55.869400  37.664400   
109  55.678000                Profsoyuznaya  55.678000  37.562700   
112  55.642800                    Belyayevo  55.642800  37.525700   
113  55.633300                      Konkovo  55.633300  37.518800   
114  55.619100                  Tyoply Stan  55.619100  37.508200   
115  55.606300                     Yasenevo  55.606300  37.533300   
117  55.860700                   Planernaya  55.860700  37.436400   
119  55.826700                  Tushinskaya  55.826700  37.436800   
121  55.808600                Shchukinskaya  55.808600  37.464100   
122  55.793500            Oktyabrskoye Pole  55.793500  37.493500   
123  55.777500              Polezhayevskaya  55.777500  37.519200   
134  55.705600                     Kuzminki  55.705600  37.765600   
135  55.717000           Ryazansky Prospekt  55.717000  37.793300   
136  55.715600                      Vykhino  55.715600  37.818100   
137  55.701300        Lermontovsky Prospekt  55.701300  37.852500   
138  55.685500                    Zhulebino  55.685500  37.856300   
139  55.674300                    Kotelniki  55.674300  37.858200   
147  55.752400                Aviamotornaya  55.752400  37.719100   
149  55.751100                       Perovo  55.751100  37.786600   
150  55.751700                 Novogireyevo  55.751700  37.816600   
151  55.745100                   Novokosino  55.745100  37.863800   
152  55.898000                    Altufyevo  55.898000  37.587000   
153  55.883800                     Bibirevo  55.883800  37.603400   
154  55.863300                    Otradnoye  55.863300  37.604700   
156  55.835100       Petrovsko-Razumovskaya  55.835100  37.574500   
157  55.817600              Timiryazevskaya  55.817600  37.576500   
170  55.652400              Sevastopolskaya  55.652400  37.598400   
171  55.640500               Chertanovskaya  55.640500  37.606700   
172  55.622400                     Yuzhnaya  55.622400  37.609000   
174  55.594900    Ulitsa Akademika Yangelya  55.594900  37.600400   
175  55.582800                       Annino  55.582800  37.596600   
176  55.569300     Bulvar Dmitriya Donskogo  55.569300  37.576900   
177 

In [29]:
merged.loc[merged['Cluster Labels'] == 4, merged.columns[[1] + list(range( merged.shape[1]))]]

Latitude        Station  Latitude  Longitude  Cluster Labels  \
21    55.6227      Salaryevo   55.6227    37.4240               4   
204   55.5821  Lesoparkovaya   55.5821    37.5769               4   
239   55.7575     Shelepikha   55.7575    37.5256               4   
241   55.7878          Zorge   55.7878    37.5045               4   

      1st Most Common Venue      2nd Most Common Venue  \
21   Furniture / Home Store              Metro Station   
204                Bus Stop  Middle Eastern Restaurant   
239           Auto Workshop              Go Kart Track   
241             Music Venue              Auto Workshop   

         3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
21                Gourmet Shop              Bus Stop         Moving Target   
204              Metro Station         Moving Target         Auto Workshop   
239                        Bar                Bakery         Grocery Store   
241  Middle Eastern Restaurant       Auto Dealership              Bus Stop   

    6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
21            Zoo Exhibit            Food Court           Fish Market   
204           Zoo Exhibit            Food Court           Fish Market   
239             Racetrack           Zoo Exhibit           Fish Market   
241           Flower Shop        Gymnastics Gym     Martial Arts Dojo   

             9th Most Common Venue 10th Most Common Venue  
21                   Fishing Store            Flea Market  
204                  Fishing Store            Flea Market  
239                  Fishing Store            Flea Market  
241  Vegetarian / Vegan Restaurant            Fish Market

In [30]:
merged.loc[merged['Cluster Labels'] == 5, merged.columns[[1] + list(range( merged.shape[1]))]]

Latitude                     Station  Latitude  Longitude  \
3     55.7888                   Sokolniki   55.7888    37.6802   
4     55.7801              Krasnoselskaya   55.7801    37.6673   
7     55.7657              Chistyye Prudy   55.7657    37.6388   
8     55.7597                    Lubyanka   55.7597    37.6272   
9     55.7577                Okhotny Ryad   55.7577    37.6166   
16    55.6926                 Universitet   55.6926    37.5333   
20    55.6330                 Rumyantsevo   55.6330    37.4419   
24    55.8549              Rechnoy Vokzal   55.8549    37.4761   
25    55.8398               Vodny Stadion   55.8398    37.4867   
26    55.8190                 Voykovskaya   55.8190    37.4980   
31    55.7701                Mayakovskaya   55.7701    37.5958   
32    55.7647                   Tverskaya   55.7647    37.6065   
33    55.7578                 Teatralnaya   55.7578    37.6190   
35    55.7305                Paveletskaya   55.7305    37.6377   
36    55.7074              Avtozavodskaya   55.7074    37.6576   
37    55.6950                  Tekhnopark   55.6950    37.6641   
49    55.8252                   Myakinino   55.8252    37.3852   
56    55.7442                  Kiyevskaya   55.7442    37.5645   
59    55.7566       Ploshchad Revolyutsii   55.7566    37.6216   
60    55.7576                    Kurskaya   55.7576    37.6577   
61    55.7730                 Baumanskaya   55.7730    37.6806   
62    55.7817           Elektrozavodskaya   55.7817    37.7037   
63    55.7833               Semyonovskaya   55.7833    37.7208   
73    55.7399                Kutuzovskaya   55.7399    37.5344   
74    55.7388              Studencheskaya   55.7388    37.5483   
75    55.7483             Mezhdunarodnaya   55.7483    37.5339   
76    55.7502               Vystavochnaya   55.7502    37.5408   
77    55.7436                  Kiyevskaya   55.7436    37.5655   
81    55.7446                  Kiyevskaya   55.7446    37.5644   
87    55.7570                    Kurskaya   55.7570    37.6595   
88    55.7418                  Taganskaya   55.7418    37.6517   
89    55.7318                Paveletskaya   55.7318    37.6379   
95    55.8552                    Sviblovo   55.8552    37.6527   
98    55.8088              Alekseyevskaya   55.8088    37.6390   
99    55.7936                   Rizhskaya   55.7936    37.6362   
102   55.7661               Turgenevskaya   55.7661    37.6374   
103   55.7553                 Kitay-gorod   55.7553    37.6333   
106   55.7198               Shabolovskaya   55.7198    37.6083   
111   55.6571                 Kaluzhskaya   55.6571    37.5405   
118   55.8505               Skhodnenskaya   55.8505    37.4396   
126   55.7612                Barrikadnaya   55.7612    37.5795   
127   55.7650                Pushkinskaya   55.7650    37.6079   
128   55.7606              Kuznetsky Most   55.7606    37.6259   
129   55.7553                 Kitay-gorod   55.7553    37.6333   
130   55.7402                  Taganskaya   55.7402    37.6522   
131   55.7319               Proletarskaya   55.7319    37.6659   
145   55.7411               Marksistskaya   55.7411    37.6543   
158   55.8069                Dmitrovskaya   55.8069    37.5817   
159   55.7927               Savyolovskaya   55.7927    37.5885   
161   55.7708             Tsvetnoy Bulvar   55.7708    37.6187   
162   55.7644                Chekhovskaya   55.7644    37.6097   
166   55.7087                    Tulskaya   55.7087    37.6229   
173   55.6124                  Prazhskaya   55.6124    37.6044   
185   55.7688                    Trubnaya   55.7688    37.6200   
186   55.7668            Sretensky Bulvar   55.7668    37.6392   
187   55.7565                Chkalovskaya   55.7565    37.6573   
189   55.7331       Krestyanskaya Zastava   55.7331    37.6673   
191   55.7074              Kozhukhovskaya   55.7074    37.6851   
213   55.8218  Ulitsa Akademika Korolyova   55.8218    37.6269   
223   55.7886                   Izmaylovo   5

In [31]:
merged.loc[merged['Cluster Labels'] == 6, merged.columns[[1] + list(range( merged.shape[1]))]]

Empty DataFrame
Columns: [Latitude, Station, Latitude, Longitude, Cluster Labels, 1st Most Common Venue, 2nd Most Common Venue, 3rd Most Common Venue, 4th Most Common Venue, 5th Most Common Venue, 6th Most Common Venue, 7th Most Common Venue, 8th Most Common Venue, 9th Most Common Venue, 10th Most Common Venue]
Index: []